<a href="https://colab.research.google.com/github/nitsundon/Load-Forecast/blob/main/XGBoostModel.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [22]:
import pandas as pd
import drive.MyDrive.Libraries.wrldc_file_handler as wfh
import xgboost as xgb
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_absolute_error
import numpy as np

import plotly.express as px

In [23]:
df4= pd.read_pickle("/content/drive/MyDrive/Libraries/pickle/preprocessed_demand_df.pkl")

In [25]:
df7=df4[~df4['demand'].isna()].copy()
wfh.add_datetime_features(df7)
df7['lag_1'] = df7['demand'].shift(1)
df7['lag_2'] = df7['demand'].shift(96)
df7['lag_3'] = df7['demand'].shift(672)
split_ratio = 1
split_index = int(len(df7) * split_ratio)

train, test = df7[:split_index], df7[split_index:]
X=train[[ 'Hour', 'DayOfWeek', 'Month', 'Quarter', 'Year',
       'DayOfyear', 'DayOfmonth', 'WeekOfYear', 'BlockNumber','lag_1','lag_2','lag_3']]
Y=train['demand']
X_test=test[[ 'Hour', 'DayOfWeek', 'Month', 'Quarter', 'Year',
       'DayOfyear', 'DayOfmonth', 'WeekOfYear', 'BlockNumber','lag_1','lag_2','lag_3']]
y_test=test['demand']
model = xgb.XGBRegressor(objective='reg:squarederror', n_estimators=100, learning_rate=0.1, max_depth=5)

# Train Model
model.fit(X,Y)

# Make Predictions
y_pred = model.predict(X_test)

if split_ratio<1:
  # Evaluate Performance
  mae = mean_absolute_error(y_test, y_pred)
  print(f'Mean Absolute Error: {mae}')
  mape = mean_absolute_percentage_error(y_test, y_pred)
  print(f'MAPE: {mape:.2f}%')


In [26]:
df8=df4[~df4['demand'].isna()].copy()

print(df8)
last_datetime = df8['datetime'].max()
future_datetimes = pd.date_range(start=last_datetime + pd.Timedelta(minutes=15), periods=96, freq='15min')
for i in range(96):
  df8=df8[['datetime','demand']]
  new_row = {
            'datetime': pd.to_datetime(future_datetimes[i]),
            'demand': 0  # or np.nan if using numpy
        }
  new_row_df = pd.DataFrame([new_row])

  df8 = pd.concat([df8, new_row_df], ignore_index=True)
  wfh.add_datetime_features(df8)
  df8['lag_1'] = df8['demand'].shift(1)
  df8['lag_2'] = df8['demand'].shift(96)
  df8['lag_3'] = df8['demand'].shift(672)
  input=df8.tail(1)[[ 'Hour', 'DayOfWeek', 'Month', 'Quarter', 'Year',
       'DayOfyear', 'DayOfmonth', 'WeekOfYear', 'BlockNumber','lag_1','lag_2','lag_3']]
  output= model.predict(input)
  df8.at[df8.index[-1], 'demand'] = output[0]

                  datetime        demand
0      2022-01-01 00:00:00  15798.000000
1      2022-01-01 00:15:00  15775.333333
2      2022-01-01 00:30:00  15667.285714
3      2022-01-01 00:45:00  15813.000000
4      2022-01-01 01:00:00  15837.000000
...                    ...           ...
114469 2025-04-07 09:00:00  26466.300000
114470 2025-04-07 09:15:00  26936.400000
114471 2025-04-07 09:30:00  27271.727273
114472 2025-04-07 09:45:00  27552.900000
114473 2025-04-07 10:00:00  27779.500000

[113775 rows x 2 columns]


In [27]:
df9=df4[~df4['demand'].isna()].copy()
# df9=df9.iloc[-96:]
# df10=df8[['datetime', 'demand']].iloc[-96:]
# df10.columns=['datetime', 'prediction']
# df9=df9.merge(df10, on='datetime')
import plotly.express as px
fig = px.line(df9, x="datetime", y=["demand"],
              title="State Demand Over Time (15-Min Blocks)",
              labels={"Timestamp": "Time", "Demand_MW": "Demand (MW)"},
              template="plotly_dark")  # Optional: Use "seaborn" or "simple_white" theme
fig.update_yaxes(range=[0, 35000])
# Show interactive graph
fig.show()